#I. Quick Setups

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3aietf%3awg%3aoauth%3a2.0%3aoob&scope=email%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdocs.test%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive.photos.readonly%20https%3a%2f%2fwww.googleapis.com%2fauth%2fpeopleapi.readonly%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive.activity.readonly%20https%3a%2f%2fwww.googleapis.com%2fauth%2fexperimentsandconfigs%20https%3a%2f%2fwww.googleapis.com%2fauth%2fphotos.native&response_type=code

Enter your authorization code:
4/1AX4XfWjis-LQ9OIF0unUuU16CuhhRrXqod3gfcg6fGBYysGsLDeWQT5jlHw
Mounted at /content/drive


In [ ]:
!pwd

/content


In [ ]:
gpu_info = !nvidia-smi
gpu_info = '\n'.join(gpu_info)
if gpu_info.find('failed') >= 0:
  print('Select the Runtime > "Change runtime type" menu to enable a GPU accelerator, ')
  print('and then re-execute this cell.')
else:
  print(gpu_info)

Thu Aug 12 01:59:08 2021       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 470.42.01    Driver Version: 460.32.03    CUDA Version: 11.2     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  Tesla P100-PCIE...  Off  | 00000000:00:04.0 Off |                    0 |
| N/A   40C    P0    27W / 250W |      0MiB / 16280MiB |      0%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
                                                                               
+-------

In [ ]:
from psutil import virtual_memory
ram_gb = virtual_memory().total / 1e9
print('Your runtime has {:.1f} gigabytes of available RAM\n'.format(ram_gb))

if ram_gb < 20:
  print('To enable a high-RAM runtime, select the Runtime > "Change runtime type"')
  print('menu, and then select High-RAM in the Runtime shape dropdown. Then, ')
  print('re-execute this cell.')
else:
  print('You are using a high-RAM runtime!')

Your runtime has 13.6 gigabytes of available RAM

To enable a high-RAM runtime, select the Runtime > "Change runtime type"
menu, and then select High-RAM in the Runtime shape dropdown. Then, 
re-execute this cell.


#II. Set up Model from hpc

Model is zipped and uploaded to MyDrive/Research/ner/text_classifier/model_env

In the future can link google drive workspace to HPC

In [ ]:
%env HOME=/content/drive/MyDrive/
#Enter Model Environment
%cd ~/Research/ner/text_classifier/model_env/dstc10
!ls -lrt

env: HOME=/content/drive/MyDrive/
/content/drive/MyDrive/Research/ner/text_classifier/model_env/dstc10
total 427984
-rw------- 1 root root       699 Jul 27 13:10 config.json
-rw------- 1 root root 437990081 Jul 27 13:10 pytorch_model.bin
-rw------- 1 root root         0 Aug  7 12:30 merge_log.txt
-rw------- 1 root root    142175 Aug  9 10:34 one_elem_cluster2.pkl
-rw------- 1 root root    121615 Aug  9 10:34 one_elem_cluster1.pkl


In [ ]:
import torch

model_name = "bert-base-uncased"
batch_size = 32
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

In [ ]:
!pip install transformers

In [ ]:
#Loading Tokenizer, Config, and Model from drive
from transformers import AutoConfig, AutoTokenizer, AutoModel, AutoModelForSequenceClassification

model_name = "bert-base-uncased"

config = AutoConfig.from_pretrained(model_name)
tokenizer = AutoTokenizer.from_pretrained(model_name, use_fast=True)
#model = AutoModel.from_pretrained("./glue_model")
model = AutoModelForSequenceClassification.from_pretrained(".")

# Set device
model.to(device)

In [ ]:
#Checks for dict weight
state_dict = model.state_dict()
state_dict["bert.embeddings.word_embeddings.weight"]

#III. Simple pair testing

In [ ]:
#result = tokenizer([(sentence, body)], return_tensors="pt", add_special_tokens=True, return_special_tokens_mask=False, padding=True)
def _single_test(pair):
    result = tokenizer([pair], return_tensors="pt")
    result.to(device)
    model.eval()
    outputs = model(**result)
    #print("Output Dictionary Keys:\n", outputs.keys(),end='\n\n')
    #print("Sequence Logits:\n",outputs,end='\n\n')
    predictions = outputs.logits.argmax(dim=-1)
    #print('Preditions:\n',predictions,end='\n\n')
    if predictions==0:
        print('True')
    else:
        print('False')
    torch.cuda.empty_cache()

In [ ]:
#Try test sets here
sentence = "Can I check in anytime?"#"When can I check-in?"
body = "Yes, 24 Hours Front Desk Avaliable."#The check."
pair = (sentence, body)
_single_test(pair)

True


Note: The result of this model is reversed due to a mistake in defining label classes

=> True : 0 (Valid)


=> False : 1 (Not Valid)

#IV. Using Model to Merge Clusters from DSTC9

In [ ]:
%cd ~/Research/ner/text_classifier
!ls -lrt

/content/drive/MyDrive/Research/ner/text_classifier
total 522053
drwx------ 2 root root      4096 Jul 16 07:26 dstc9_bertemb
-rw------- 1 root root      7241 Jul 19 11:29 knowledge_db.py
-rw------- 1 root root     25673 Jul 26 09:40 Process_clean_v2.py
-rw------- 1 root root      9143 Jul 26 10:27 example_generation_methods.py
-rw------- 1 root root  78256603 Jul 26 10:41 classifier_examples.json
-rw------- 1 root root 405246184 Jul 28 13:35 text_classification_model.zip
drwx------ 3 root root      4096 Jul 28 13:56 model_env
-rw------- 1 root root  12027543 Jul 29 15:16 kb_eval_ex.json
-rw------- 1 root root  12642400 Jul 29 15:19 kb_eval_ex_new.json
-rw------- 1 root root      1220 Aug  5 06:21 old_main_merge.py
-rw------- 1 root root    389296 Aug  5 15:15 reverse_merged_kb_doc_clusters.pkl
-rw------- 1 root root   1212770 Aug  7 15:19 _merge_result.txt
-rw------- 1 root root    263057 Aug  7 16:14 __new_merged_kb_doc_clusters1.pkl
-rw------- 1 root root    253841 Aug  7 16:59 __new

## Add doc_ids to kb_eval_ex.json to make search easier

In [ ]:
#@title KB Modification
import json

def main():
    kb = open('kb_eval_ex.json','r')
    out = open('kb_eval_ex_new.json','w')
    dic = json.load(kb)

    for cat in dic:
        for elem in dic[cat]:
            for entry in dic[cat][elem]['docs']:
                doc_id='_'.join([cat,elem,entry])
                dic[cat][elem]['docs'][entry]['doc_id']=doc_id
                print(doc_id)

    json.dump(dic,out,indent=4)

if __name__=='__main__':
    main()

## Initialize Clusters and KB

In [ ]:
#Get Cluster Maps
import pickle

og_cluster1 = {}
og_cluster2 = {}
with open('kb_doc_clusters.pkl','rb') as F:
    pickle_obj1 = pickle.load(F)
    F.close()
with open('kb_doc_clusters2.pkl','rb') as F:
    pickle_obj2 = pickle.load(F)
    F.close()
lst1 = [elem for elem in pickle_obj1 if len(elem)>0]#title matches
lst2 = [elem for elem in pickle_obj2 if len(elem)>0]#body matches

for i in range(len(lst1)):
    og_cluster1[i] = lst1[i]
for j in range(len(lst2)):
    og_cluster2[j] = lst2[j]


In [ ]:
#Check
print(og_cluster1, len(og_cluster1), sep = '\n')
print(og_cluster2, len(og_cluster2), sep = '\n')

{0: {'hotel_23_4', 'hotel_0_0', 'hotel_29_17', 'hotel_8_8'}, 1: {'hotel_0_2'}, 2: {'hotel_0_7'}, 3: {'hotel_0_9'}, 4: {'hotel_0_10', 'hotel_110090_16', 'hotel_110176_14', 'restaurant_19237_9'}, 5: {'hotel_21_18', 'hotel_0_18', 'hotel_28_9', 'hotel_24_31'}, 6: {'hotel_29_6', 'hotel_0_19'}, 7: {'hotel_0_20'}, 8: {'hotel_0_24'}, 9: {'hotel_0_25'}, 10: {'hotel_0_26'}, 11: {'hotel_0_27', 'hotel_110139_9'}, 12: {'hotel_0_30', 'hotel_110115_24'}, 13: {'hotel_0_34'}, 14: {'hotel_1_0', 'hotel_110077_0'}, 15: {'hotel_1_3'}, 16: {'hotel_1_5', 'hotel_12_0'}, 17: {'hotel_1_6'}, 18: {'hotel_1_8'}, 19: {'hotel_1_10', 'hotel_110175_24'}, 20: {'hotel_1_11'}, 21: {'hotel_110167_17', 'hotel_110034_24', 'hotel_110063_15', 'hotel_110054_17', 'hotel_110047_17', 'hotel_110066_23', 'hotel_110020_13', 'hotel_28_36', 'hotel_19_34', 'hotel_110039_20', 'hotel_110115_22', 'hotel_1_12', 'hotel_110016_16', 'hotel_110048_23'}, 22: {'hotel_10_20', 'hotel_1_17'}, 23: {'hotel_1_19'}, 24: {'hotel_1_26'}, 25: {'hotel_1_29

In [ ]:
#Get Knowledge Base
import json

kb = open('kb_eval_ex_new.json','r')
dic = json.load(kb)

In [ ]:
#Check
elem = dic['hotel']['0']['docs']['0']
print(elem['title_ex'],elem['body_ex'],sep='\n')

Are children welcomed?
Yes, you can stay with children.


Format of Cluster Map:
dictionary of id : set of doc_ids

res = {     i:{'hotel_id_docid', ... }, { ... }, ...     }

----------------
Format of KB:
{'category': {'id': {'name': "", 'docs': { 'doc_id': {'title': "", 'body': ""}}}}}

the "title_ex" and "body_ex" fields were used as examples to train the model (delexicalized)

## Random Sampling

In [ ]:
#Random Sampling Test
import random

#Get all the possible keys for random sampling
cluster_key_lst1 = [x for x in og_cluster1.keys() if len(og_cluster1[x]) > 0]
cluster_key_lst2 = [y for y in og_cluster2.keys() if len(og_cluster2[y]) > 0]

#Select one key to sample from
cluster_key1 = 109#random.choice(cluster_key_lst1)
cluster_key2 = 326#random.choice(cluster_key_lst2)

title_set = og_cluster1[cluster_key1]
body_set = og_cluster2[cluster_key2]
print('Title Set size:', len(title_set))
print(title_set)
print('\nBody Set size:', len(body_set))
print(body_set,'\n')

title_lst = []
body_lst = []
pair_lst = []
id_pair_lst = []
tdups = 0
n = 0

#Sampling pairs from clusters/kb
#Method outdated, need to renew

for n in range(n,len(title_set)):
    #allow maximum of _ title to sample
    if n - tdups == 4:
        break
    title_id=title_set.pop()
    tcat,tid,tdoc_id = title_id.split('_')
    title_ex = dic[tcat][tid]['docs'][tdoc_id]['title_ex']

    #if already a title, don't want to duplicates
    if title_ex in title_lst:
        tdups += 1
        continue
    else:
        title_lst.append(title_ex)

    body_count = 0
    bdups = 0
    for elem in body_set:
        #only want a maximum of _ to match with a title 
        if body_count == 3:
            break

        body_id = elem
        bcat,bid,bdoc_id = body_id.split('_')
        body_ex = dic[bcat][bid]['docs'][bdoc_id]['body_ex']
        
        #if already a body, don't want duplicates
        if body_ex in body_lst:
            bdups += 1
            continue
        else:
            body_lst.append(body_ex)
            body_count += 1

        #Add pair to list for eval
        pair = (title_ex, body_ex)
        id_pair = (title_id, body_id)
        #print(pair,'\n')
        pair_lst.append(pair)
        id_pair_lst.append(id_pair)


#Tokenize pairs, then send to model
results = tokenizer(pair_lst, return_tensors="pt", padding=True, truncation=True)
results.to(device)

#Evaluate
model.eval()
outputs = model(**results)
predictions = outputs.logits.argmax(dim=-1)
print('Title Duplicates:',tdups,'\tOnly ',len(title_lst),'sampled\n')
print('Body Duplicates:', bdups ,'\tOnly ',len(body_lst), 'sampled\n')

print('Preditions:\n',predictions,'\n')

#Output corresponding pairs and prediction results 
count = 0
for p in predictions:
    print('#', count, '------------------------------------\n')
    print('title:\t', pair_lst[count][0], '(', id_pair_lst[count][0], ')')
    print('body:\t', pair_lst[count][1], '(', id_pair_lst[count][1], ')')
    print('\nResult: ',end='')
    if p==1:
        print('Not Valid\n')
    else:
        print('Valid\n')
    count += 1

In [ ]:
#Clear cuda memory
torch.cuda.empty_cache()

## Cluster length info

In [ ]:
#Info on length of clusters of res1
print(og_cluster1)
w = [cl for cl in og_cluster1 if len(og_cluster1[cl]) > 0]
print(len(w))
for cl in w:
    print(len(og_cluster1[cl]),end=', ')

In [ ]:
#Info on length of clusters of res2
print(og_cluster2)
w = [cl for cl in og_cluster2 if len(og_cluster2[cl]) > 0]
print(len(w))
for cl in w:
    print(len(og_cluster2[cl]),end=', ')

## Methods

In [ ]:
#Method for Find particular key for og_cluster1
def _find_key(id, cluster):
    cluster_key_lst = [x for x in cluster.keys() if len(cluster[x]) > 0]
    key_lst = []
    for key in cluster_key_lst:
        for elem in cluster[key]:
            if id in elem:
                key_lst.append(key)
    if len(key_lst) == 0:
        return None
    return key_lst

In [ ]:
#Extra Method for immediate testing or use
def _get_title_body_pair(dic, doc_id):
    #gets title_ex and body_ex
    cat,id,d_id = doc_id.split('_')
    body_ex = dic[cat][id]['docs'][d_id]['body_ex']
    title_ex = dic[cat][id]['docs'][d_id]['title_ex']
    return (title_ex, body_ex)
def _get_title_lst(res, key):
    title_lst = {}
    for res_elem in res[key]:
        tcat,tid,tdoc_id = res_elem.split('_')
        title_ex = dic[tcat][tid]['docs'][tdoc_id]['title_ex']

        #Avoid Duplicates
        if title_ex not in title_lst:
            title_lst[title_ex] = [res_elem]
        else:
            title_lst[title_ex].append(res_elem)
            continue
    return title_lst 
def _get_body_lst(res, key):
    body_lst = {}
    for res_elem in res[key]:
        bcat,bid,bdoc_id = res_elem.split('_')
        body_ex = dic[bcat][bid]['docs'][bdoc_id]['body_ex']

        #Avoid Duplicates
        if body_ex not in body_lst:
            body_lst[body_ex] = [res_elem]
        else:
            body_lst[body_ex].append(res_elem)
            continue
    return body_lst

In [ ]:
#Extra Methods for Getting Merge Map
import time

def _do_eval(pair_lst):
    #Tokenize all the pairs and send to device
    results = tokenizer (pair_lst, return_tensors = 'pt', padding = True, truncation = True)
    results.to(device)
    
    #Evaluate
    model.eval()
    with torch.no_grad():
        outputs = model(**results)
    predictions = outputs.logits.argmax(dim=-1)

    #Clear cuda memory
    torch.cuda.empty_cache()

    valid = 0
    total = 0
    #Compute Score. Change accordingly
    for p in predictions:
        if p == 0:
            valid += 1
        total += 1
    
    return (valid/total)


def _merge_match(ftitle_lst, fbody_lst, btitle_lst, bbody_lst, batch_size, threshold, tweek, manual):
    '''
    In: {title : doc_id}, {body : doc_id}, size per training
    Out: bool, True = Merge
    '''
    og_threshold = threshold
    pair_lst = []
    count = 0
    last_score = None

    for ftitle in ftitle_lst:
        for fbody in fbody_lst:
            if last_score is not None:
                if last_score == 1:
                    if count >= 200:
                        print('!EARLY MERGE\t LAST SCORE: ', score, '>', threshold, '------')
                        return True
                    threshold -= 2*tweek
                elif last_score > 0.85:
                    threshold -= tweek
            if len(pair_lst) >= batch_size:
                score = _do_eval(pair_lst)
                print('----------------------------')
                print('Size:\t', len(pair_lst))
                print('Contents:\n', pair_lst[0:10])#[ex for ex in pair_lst]

                #Decide base on score
                if score < threshold:
                    print('NO MERGE\t\t------')
                    print('SCORE ONLY\t', score, '<', threshold, '\n\n')
                    if score > manual:
                        x = input('Force Merge? (f)')
                        if x == 'f':
                            return True
                    return False
                else:
                    last_score = score

                #Clear list
                pair_lst = []

            pair = (ftitle, fbody)
            pair_lst.append(pair)
            count += 1

    for btitle in btitle_lst:
        for bbody in bbody_lst:
            if last_score is not None:
                if last_score == 1:
                    if count >= 200:
                        print('!EARLY MERGE\t LAST SCORE: ', score, '>', threshold, '------')
                        return True
                    threshold -= 2*tweek
                elif last_score > 0.85:
                    threshold -= tweek
                elif last_score < og_threshold:
                    threshold += 3*tweek
            if len(pair_lst) >= batch_size:
                score = _do_eval(pair_lst)
                print('----------------------------')
                print('Size:\t', len(pair_lst))
                print('Contents:\n', pair_lst[0:10])#[ex for ex in pair_lst]

                #Decide base on score
                if score < threshold:
                    print('NO MERGE\t\t------')
                    print('SCORE ONLY\t', score, '<', threshold, '\n\n')
                    if score > manual:
                        x = input('Force Merge? (f)')
                        if x == 'f':
                            return True
                        return False
                else:
                    last_score = score
                #Clear list
                pair_lst = []

            pair = (btitle, bbody)
            pair_lst.append(pair)
            count += 1


    #If not enough matching examples, do not merge. Change accordingly
    if count<2:
        print('!!!!!\t\tNOT ACCEPTED\t\t!!!!!------')
        print(ftitle_lst, fbody_lst)
        print(btitle_lst, bbody_lst)
        print('\nONLY\t', count, '\tEXAMPLES\n\n')
        return False
    
    #Final Batch to Evaluate
    score = _do_eval(pair_lst)
    print(count, 'examples -------------------')
    print('Size:\t', len(pair_lst))
    print('Contents:\n', pair_lst[0:10])#[ex for ex in pair_lst]
    if score < threshold:
        print('NO MERGE\t\t------')
        print('SCORE ONLY\t', score, '<', threshold, '\n\n')
        if score > manual:
            x = input('Force Merge? (f)')
            if x == 'f':
                return True
        return False
    print('!MERGE\t LAST SCORE: ', score, '>', threshold, '------')
    #time.sleep(3)
    return True



In [ ]:
#Get Main Merge Eval Function
import time
from IPython.display import clear_output 

def _reorder_cluster(cluster):
    id = 1#we need 0 to be the invalids
    res_cluster = {}
    for key in cluster:
        res_cluster[id] = cluster[key]
        id += 1
    return res_cluster

def _merge_eval(res1, res2, diff = False, batch_size = 500, threshold = 0.8, skip_ambig = False, manual = 1):
    #These methods are predefined but realistically they should be in here
    def _get_title_lst(res, key):
        title_lst = {}
        for res_elem in res[key]:
            tcat,tid,tdoc_id = res_elem.split('_')
            title_ex = dic[tcat][tid]['docs'][tdoc_id]['title_ex']
    
            #Avoid Duplicates
            if title_ex not in title_lst:
                title_lst[title_ex] = [res_elem]
            else:
                title_lst[title_ex].append(res_elem)
                continue
        return title_lst 
    def _get_body_lst(res, key):
        body_lst = {}
        for res_elem in res[key]:
            bcat,bid,bdoc_id = res_elem.split('_')
            body_ex = dic[bcat][bid]['docs'][bdoc_id]['body_ex']
    
            #Avoid Duplicates
            if body_ex not in body_lst:
                body_lst[body_ex] = [res_elem]
            else:
                body_lst[body_ex].append(res_elem)
                continue
        return body_lst
    ignore_lst = []
    ambig_lst = [46,50,70,80,100,104]#[57,64,91,104,130,134]#refer to onenote
    cluster_key_lst1 = [x for x in res1.keys() if len(res1[x]) > 0]
    cluster_key_lst2 = [y for y in res2.keys() if len(res2[y]) > 0]

    for key1 in cluster_key_lst1:
        if skip_ambig and key1 in ambig_lst:
            continue
        if not diff:
            if key1 in ignore_lst:
                continue
        merge = False
        #Implement Reverse Matching
        forward_title_lst = _get_title_lst(res1, key1)
        backward_body_lst = _get_body_lst(res1, key1)
        
        #For each body cluster, retrieve body list and compute metric
        if not diff:
            start = key1 + 1
        else:
            start = 0
        for i in range(start, len(cluster_key_lst2)):
            if i%5 == 0:
                #time.sleep(8)
                clear_output()
            key2 = cluster_key_lst2[i]
            if key2 in ignore_lst:
                continue
            forward_body_lst = _get_body_lst(res2, key2)
            backward_title_lst = _get_title_lst(res2, key2)
            merge = _merge_match(forward_title_lst, forward_body_lst, backward_title_lst, backward_body_lst, batch_size, threshold, 0.001, manual)#batch size per eval
            if merge:
                res1[key1] |= res2[key2]#_main_merge(res1, res2, key1, key2)
                if key2 not in ignore_lst:
                    ignore_lst.append(key2)#add to ignore list
                print(res1[key1], ignore_lst, sep = '\n')
                print(len(res1) - len(ignore_lst))
                #time.sleep(2)
    #Final deletions(for merging within same cluster)
    if not diff:
        for elem in ignore_lst:
            res1.pop(elem)
    else:
        start_id = len(res1)
        for elem in cluster_key_lst2:
            if elem not in ignore_lst:
                res1[start_id] = res2[elem]
                start_id += 1
    print('Length of Final Cluster:\t', len(res1))
    return res1

In [ ]:
#Output function
import pickle

def _store_cluster(final_cluster, outfile):    
    print(final_cluster)
    with open(outfile, "wb") as F:
        pickle.dump(final_cluster, F)
    F.close()
    print('Done')

## Executes

#### Title Cluster - og_cluster1

In [ ]:
merged_cluster1 = _merge_eval(og_cluster1, og_cluster1, threshold=0.98)
_store_cluster(merged_cluster1, 'V1_merged_kb_doc_clusters1.pkl')

6 examples -------------------
Size:	 6
Contents:
 ('Are children welcomed?', 'It does not offer live music.')
NO MERGE		------
SCORE ONLY	 0.0 < 0.98 




KeyboardInterrupt: ignored

In [ ]:
#logs = open('merge_log.txt','a')
#merged_cluster1 = _merge_eval(og_cluster1, og_cluster1)
#_store_cluster(merged_cluster1, 'new_merged_kb_doc_clusters1.pkl')

#After implementing reverse matching. Also implement the score threshold manuel controls for each merge process
merged_cluster1 = _merge_eval(og_cluster1, og_cluster1, threshold=0.80)
_store_cluster(merged_cluster1, '_new_merged_kb_doc_clusters1.pkl')

#### Body Cluster - og_cluster2

In [ ]:
merged_cluster2 = _merge_eval(og_cluster2, og_cluster2, threshold=0.98)
_store_cluster(merged_cluster2, 'V1_merged_kb_doc_clusters2.pkl')

In [ ]:
#logs = open('merge_log.txt','a')
#merged_cluster2 = _merge_eval(og_cluster2, og_cluster2)
#_store_cluster(merged_cluster2, 'new_merged_kb_doc_clusters2.pkl')

merged_cluster2 = _merge_eval(og_cluster2, og_cluster2, threshold=0.80)
_store_cluster(merged_cluster2, '_new_merged_kb_doc_clusters2.pkl')

#### Retrieve merged_cluster 1 and 2

In [ ]:
with open('V1_merged_kb_doc_clusters1.pkl','rb') as F:
    merged_cluster1 = pickle.load(F)
print(merged_cluster1, len(merged_cluster1), sep = '\n')

with open('V1_merged_kb_doc_clusters2.pkl','rb') as F:
   merged_cluster2 = pickle.load(F)
print(merged_cluster2, len(merged_cluster2), sep = '\n')


#### Check keys, length info, and then Reorder

In [ ]:
for key in merged_cluster1:
    print(key, end = ' ')
print('\n')
for key in merged_cluster2:
    print(key, end = ' ')

NameError: ignored

In [ ]:
w = [cl for cl in merged_cluster1 if len(merged_cluster1[cl]) > 50]
print(len(w))
for cl in w:
    print(len(merged_cluster1[cl]),end=', ')

NameError: ignored

In [ ]:
w = [cl for cl in merged_cluster2 if len(merged_cluster2[cl]) > 50]
print(len(w))
for cl in w:
    print(len(merged_cluster2[cl]),end=', ')

In [ ]:
fmerged_cluster1 = _reorder_cluster(merged_cluster1)
fmerged_cluster2 = _reorder_cluster(merged_cluster2)

print(fmerged_cluster1, len(fmerged_cluster1), sep = '\n')
print(fmerged_cluster2, len(fmerged_cluster2), sep = '\n')

In [ ]:
#Check cluster reordering function
for key in fmerged_cluster1:
    print(key, end = ' ')
print('\n')
for key in fmerged_cluster2:
    print(key, end = ' ')

#### Final Merge the two merged clusters

In [ ]:
final_cluster1 = _merge_eval(fmerged_cluster1, fmerged_cluster2, True, threshold=0.80)
_store_cluster(final_cluster1, 'V1_final1_merged_kb_doc_clusters.pkl')

In [ ]:
#logs = open('merge_log.txt','a')
#final_cluster1 = _merge_eval(fmerged_cluster1, fmerged_cluster2, True)
#_store_cluster(final_cluster1, 'final1_merged_kb_doc_clusters.pkl')

final_cluster1 = _merge_eval(fmerged_cluster1, fmerged_cluster2, True, threshold=0.85)
_store_cluster(final_cluster1, '_final1_merged_kb_doc_clusters.pkl')

In [ ]:
#was 109
for key in final_cluster1:
    print(key, end = ' ')
print('\n')
print(final_cluster1, len(final_cluster1), sep = '\n')

#### Additional Self Merge on final_cluster1

In [ ]:
final_cluster2 = _merge_eval(final_cluster1, final_cluster1, threshold=0.8)
_store_cluster(final_cluster2, '__final2_merged_kb_doc_clusters.pkl')

In [ ]:
#Now with more examples to generate per cluster, might boost some scores for further merging
#logs = open('merge_log.txt','a')
#final_cluster2 = _merge_eval(final_cluster1, final_cluster1)
#_store_cluster(final_cluster2, 'final2_merged_kb_doc_clusters.pkl')

final_cluster2 = _merge_eval(final_cluster1, final_cluster1, threshold=0.85)
_store_cluster(final_cluster2, '_final2_merged_kb_doc_clusters.pkl')

In [ ]:
print(final_cluster2, len(final_cluster2), sep = '\n')#Was 86, Now 104

### Debugging

In [ ]:
#Simple Cluster Example
m = {0:[0,2], 1:[1] ,2:[1,2]}
cl1 = {0:{'hotel0'},1:{'hotel1'},2:{'hotel2'}}
cl2 = {0:{'hotel0'},1:{'hotel1'},2:{'hotel2'}}

fi = _main_merge(cl1,cl2,m)
print(fi, len(fi),sep = '\n')

In [ ]:
#Tests on Final Cluster
import pickle

with open('fmerged_kb_doc_clusters.pkl','rb') as F:
    pickle_obj = pickle.load(F)

print(pickle_obj, len(pickle_obj), sep = '\n')

elem_lst = []
x = 0
for key in pickle_obj:
    if pickle_obj[key] not in elem_lst:
        elem_lst.append(pickle_obj[key])
        x += 1
print(x)

In [ ]:
#Some other Debugs
x = {0:[1],2:[3]}
cl1 = {0:{'hotel1','hotel3'},1:{'hotel2'},2:{'hotel5'}}
cl2 = {0:{'hotel80'},1:{'hotel2'},2:{'hotel11'},3:{'hotel9'}}
xx = _main_merge(cl1, cl2, x)
print(xx)
_store_cluster(xx, 'testxx.pkl')

### Abandoned

In [ ]:
#Start Clean Up/Merging within the two og_clusters (abandoned approach)
import time
'''

'''
logs = open('merge_log.txt','a')

map1 = _get_merge_map(og_cluster1, og_cluster1)
merged_cluster1 = _main_merge(og_cluster1, og_cluster1, map1)
_store_cluster(merged_cluster1, 'merged_kb_doc_clusters1.pkl')

print('Finished Cleaning og_cluster1.')
logs.write('\nX\nFinished Cleaning og_cluster1.\nX\n')

time.sleep(5)
'''
map2 = _get_merge_map(og_cluster2, og_cluster2)
merged_cluster2 = _main_merge(og_cluster2, og_cluster2, map2)
_store_cluster(merged_cluster2, 'merged_kb_doc_clusters2.pkl')

print('Finished Cleaning og_cluster2.')
logs.write('\nX\nFinished Cleaning og_cluster2.\nX\n')

time.sleep(5)

#Then Start Merging the two

p_map = _get_merge_map(merged_cluster1, merged_cluster2)

p_cluster = _main_merge(merged_cluster1, merged_cluster2, p_map)
_store_cluster(p_cluster, 'pmerged_kb_doc_clusters.pkl')

print('Finished Merging premature_cluster.')
logs.write('\nX\nFinished Merging premature_cluster.\nX\n')

time.sleep(5)

#Final Merge
final_map = _get_merge_map(p_cluster, p_cluster)

final_cluster = _main_merge(p_cluster, p_cluster, final_map)
_store_cluster(final_cluster, 'fmerged_kb_doc_clusters.pkl')

print('Finished Cleaning final_cluster.')
logs.write('\nX\nFinished Cleaning final_cluster.\nX\n')

time.sleep(5)
'''

#V. Merge Output Tests

## Initialize if already produced/merged

In [ ]:
with open('__final1_merged_kb_doc_clusters.pkl','rb') as f:
    final_cluster1 = pickle.load(f)
with open('__final2_merged_kb_doc_clusters.pkl','rb') as f:
    final_cluster2 = pickle.load(f)
with open('__final3_merged_kb_doc_clusters.pkl','rb') as f:
    final_cluster3 = pickle.load(f)
with open('__new_merged_kb_doc_clusters1.pkl','rb') as f1:
    merged_cluster1 = pickle.load(f1)
with open('__new_merged_kb_doc_clusters2.pkl','rb') as f2:
    merged_cluster2 = pickle.load(f2)


In [ ]:
#Check
print(final_cluster1, len(final_cluster1), sep = '\n')
print(final_cluster2, len(final_cluster2), sep = '\n')
print(final_cluster3, len(final_cluster3), sep = '\n')

print(merged_cluster1, len(merged_cluster1), sep = '\n')
print(merged_cluster2, len(merged_cluster2), sep = '\n')

## Test 1: Get Merge results

In [ ]:
#Generate merge results
#import json#json not complete file?

def _get_result(out, cluster):
    f = open(out,'w')
    pair_dic = {}
    for id in cluster:
        f.write(str(id)+'-------------------\n')
        for elem in cluster[id]:
            pair = _get_title_body_pair(dic, elem)
            f.write('\t'+elem+'\n')
            f.write('\t\tTitle: '+pair[0]+'\n')
            f.write('\t\tBody: '+pair[1]+'\n')
        f.write('\n\n')
    f.close()

def main():    
    f = open('f__merge_result.txt','w')
    pair_dic = {}
    for id in final_cluster2:
        f.write(str(id)+'-------------------\n')
        for elem in final_cluster2[id]:
            pair = _get_title_body_pair(dic, elem)
            f.write('\t'+elem+'\n')
            f.write('\t\tTitle: '+pair[0]+'\n')
            f.write('\t\tBody: '+pair[1]+'\n')
        f.write('\n\n')
    f.close()           
        
    
'''
if __name__ == '__main__':
    main()
'''

"\nif __name__ == '__main__':\n    main()\n"

## Test 2: Reverse Merging

In [ ]:
reverse_cluster = _merge_eval(merged_cluster2, merged_cluster1, True)
_store_cluster(reverse_cluster, 'reverse_merged_kb_doc_clusters.pkl')
print(reverse_cluster, len(reverse_cluster), sep = '\n')#length is 114, worse than 109

----------------------------
Size:	 500
Contents:
 ('Am I allowed to stay with my children?', 'Yes, it is kid-friendly.')
----------------------------
Size:	 500
Contents:
 ('Is your cafe kid-friendly?', 'It is considered a good restaurant for kids.')


KeyboardInterrupt: ignored

## Test 3: Further Merging

In [ ]:
#logs = open('merge_log.txt','a')
final_cluster3 = _merge_eval(final_cluster2, final_cluster2, threshold = 0.7)
_store_cluster(final_cluster3, 'V1_final3_merged_kb_doc_clusters.pkl')

Length of Final Cluster:	 96
{0: {'attraction_100013_4', 'restaurant_120053_19', 'restaurant_120124_18', 'restaurant_120460_10', 'attraction_100086_0', 'hotel_4_11', 'attraction_100150_0', 'hotel_30_13', 'restaurant_120201_14', 'restaurant_120369_0', 'attraction_100087_1', 'restaurant_120200_1', 'restaurant_120390_12', 'restaurant_120328_15', 'restaurant_120496_13', 'attraction_100138_4', 'attraction_100081_0', 'restaurant_120427_13', 'attraction_100012_4', 'attraction_100131_4', 'restaurant_120116_14', 'restaurant_120064_14', 'attraction_100042_5', 'restaurant_120277_17', 'restaurant_120426_12', 'restaurant_120001_11', 'restaurant_120128_15', 'hotel_11_8', 'attraction_100001_9', 'hotel_2_12', 'restaurant_120102_17', 'restaurant_120030_17', 'attraction_100101_3', 'restaurant_120298_16', 'restaurant_120159_14', 'attraction_100197_2', 'restaurant_120130_14', 'hotel_14_20', 'attraction_100097_4', 'restaurant_120106_14', 'restaurant_120033_16', 'restaurant_120027_14', 'restaurant_120275_18

In [ ]:
print(final_cluster3, len(final_cluster3), sep = '\n')

{0: {'attraction_100013_4', 'restaurant_120053_19', 'restaurant_120124_18', 'restaurant_120460_10', 'attraction_100086_0', 'hotel_4_11', 'attraction_100150_0', 'hotel_30_13', 'restaurant_120201_14', 'restaurant_120369_0', 'attraction_100087_1', 'restaurant_120200_1', 'restaurant_120390_12', 'restaurant_120328_15', 'restaurant_120496_13', 'attraction_100138_4', 'attraction_100081_0', 'restaurant_120427_13', 'attraction_100012_4', 'attraction_100131_4', 'restaurant_120116_14', 'restaurant_120064_14', 'attraction_100042_5', 'restaurant_120277_17', 'restaurant_120426_12', 'restaurant_120001_11', 'restaurant_120128_15', 'hotel_11_8', 'attraction_100001_9', 'hotel_2_12', 'restaurant_120102_17', 'restaurant_120030_17', 'attraction_100101_3', 'restaurant_120298_16', 'restaurant_120159_14', 'attraction_100197_2', 'restaurant_120130_14', 'hotel_14_20', 'attraction_100097_4', 'restaurant_120106_14', 'restaurant_120033_16', 'restaurant_120027_14', 'restaurant_120275_18', 'restaurant_120045_13', 'r

In [ ]:
_get_result('V1_merge_result.txt', final_cluster3)

## Test 4: Cases

In [ ]:
id = "restaurant_120071_2"
key = _find_key(id, og_cluster1)
if key is not None:
    print(key)
else:
    print('Not found in cluster')

[2903, 2936]


In [ ]:
id = "restaurant_120035_19"
key = _find_key(id, og_cluster1)
if key is not None:
    print(key)
else:
    print('Not found in cluster')

[2931]


In [ ]:
id = 46
print(len(og_cluster1[id]))
for item in og_cluster1[id]:
    pair = _get_title_body_pair(dic, item)
    print(pair[0], pair[1], sep = '\n')

2
Do you offer a safety deposit box in your rooms?
It does not offer a safety deposit box.
Do you offer any safety deposit boxes in your rooms?
It does not offer safety deposit boxes in their rooms.


## Test 5: Duplicates?

In [ ]:
def finddupes(cluster):
    dupes = {}
    uniques = {}
    n = 0
    for key in cluster:
        for id in cluster[key]:
            if id not in uniques:
                n += 1
                uniques[id] = n
            elif id in dupes:
                dupes[id] += 1
            else:
                dupes[id] = 1
    print(len(uniques), dupes)
    return dupes

In [ ]:
#Looking at numbers
dupes = {}
uniques = {}
n = 0
for key in og_cluster1:
    for id in og_cluster1[key]:
        if id not in uniques:
            n += 1
            uniques[id] = n
        elif id in dupes:
            dupes[id] += 1
        else:
            dupes[id] = 1
print(len(uniques), dupes)
dupes = {}
uniques = {}
n = 0
for key in og_cluster2:
    for id in og_cluster2[key]:
        if id not in uniques:
            n += 1
            uniques[id] = n
        elif id in dupes:
            dupes[id] += 1
        else:
            dupes[id] = 1
print(n, dupes)
print(len(uniques))
print(len(dupes))

9600 {}
9177 {}
9177
0


In [ ]:
#Get duplicate map
dmap = {}

for key in final_cluster3:
    for id in final_cluster3[key]:
        first = True
        for rkey in final_cluster3:
            for rid in final_cluster3[rkey]:
                if id == rid and rkey != key:
                    if id in dmap:
                        if first:
                            dmap[id].append(key)
                            first = False
                    else:
                        if first:
                            dmap[id] = [key]
                            first = False
                    dmap[id].append(rkey)

In [ ]:
#Dupe map properties
print(len(dmap))
for id in dmap:
    if len(dmap[id]) >= 1:
        print(dmap[id])

In [ ]:
#Detailed look at duped doc_ids in final cluster
#Try to see if those clusters that has same id can be merged

for id in dmap:
    key = dmap[id].pop(0)
    print('Current: ',id)
    ogpair = _get_title_body_pair(dic, id)
    print('\t',ogpair[0])
    print('\t',ogpair[1])
    x = input('Start evaluating this? (n)')
    if x == 'n':
        for item in final_cluster3[key]:
            pair= _get_title_body_pair(dic, item)
            print('\t',pair[0])
            print('\t',pair[1])
            y=input('Next example? (n)')
            if y == 'n':
                continue
            else:
                break
        print('Now the other cluster where ',id, 'was duped:')
        count = 1
        for dupe in dmap[id]:
            print('Dupe Cluster #',count)    
            for item in final_cluster3[dupe]:
                pair = _get_title_body_pair(dic, item)
                print('\t',item)
                print('\t',pair[0])
                print('\t',pair[1])
                y=input('Next example? (n)')
                if y == 'n':
                    continue
                else:
                    break
            count += 1
                


Summary: cannot. For example running the code for the first duplicate example
restaurant_120053_19

its title and body = What is offered?
	                It is good for kid.

This doc_id is in another cluster with ambiguious titles like 'What is offered'

This needs to be refined

#VI. Missed 1 element length clusters

## Initialize the one_elem_clusters

In [ ]:
one_elem_cluster_key_lst1 = [x for x in og_cluster1.keys() if len(og_cluster1[x]) == 1]
print(len(one_elem_cluster_key_lst1))

one_elem_cluster1 = {}
id = 0
for key in one_elem_cluster_key_lst1:
    one_elem_cluster1[id] = og_cluster1[key]
    id += 1
print(one_elem_cluster1, len(one_elem_cluster1), sep = '\n')
_store_cluster(one_elem_cluster1, 'one_elem_cluster1.pkl')

2415
{0: {'hotel_1_29'}, 1: {'hotel_2_7'}, 2: {'hotel_2_10'}, 3: {'hotel_2_12'}, 4: {'hotel_2_14'}, 5: {'hotel_2_15'}, 6: {'hotel_3_7'}, 7: {'hotel_4_3'}, 8: {'hotel_4_17'}, 9: {'hotel_4_19'}, 10: {'hotel_4_22'}, 11: {'hotel_4_24'}, 12: {'hotel_4_27'}, 13: {'hotel_4_28'}, 14: {'hotel_4_35'}, 15: {'hotel_5_0'}, 16: {'hotel_5_5'}, 17: {'hotel_5_12'}, 18: {'hotel_5_18'}, 19: {'hotel_5_24'}, 20: {'hotel_6_3'}, 21: {'hotel_6_8'}, 22: {'hotel_6_14'}, 23: {'hotel_6_18'}, 24: {'hotel_6_20'}, 25: {'hotel_6_34'}, 26: {'hotel_7_8'}, 27: {'hotel_7_10'}, 28: {'hotel_7_19'}, 29: {'hotel_7_20'}, 30: {'hotel_7_25'}, 31: {'hotel_7_37'}, 32: {'hotel_8_1'}, 33: {'hotel_8_3'}, 34: {'hotel_8_5'}, 35: {'hotel_8_6'}, 36: {'hotel_8_9'}, 37: {'hotel_8_10'}, 38: {'hotel_8_11'}, 39: {'hotel_8_14'}, 40: {'hotel_8_16'}, 41: {'hotel_8_18'}, 42: {'hotel_8_20'}, 43: {'hotel_8_24'}, 44: {'hotel_8_25'}, 45: {'hotel_8_30'}, 46: {'hotel_8_31'}, 47: {'hotel_8_34'}, 48: {'hotel_9_0'}, 49: {'hotel_9_11'}, 50: {'hotel_9_12'}

In [ ]:
one_elem_cluster_key_lst2 = [x for x in og_cluster2.keys() if len(og_cluster2[x]) == 1]
print(len(one_elem_cluster_key_lst2))

one_elem_cluster2 = {}
id = 0
for key in one_elem_cluster_key_lst2:
    one_elem_cluster2[id] = og_cluster2[key]
    id += 1

print(one_elem_cluster2, len(one_elem_cluster2), sep = '\n')
_store_cluster(one_elem_cluster2, 'one_elem_cluster2.pkl')

2862
{0: {'hotel_0_2'}, 1: {'hotel_0_3'}, 2: {'hotel_0_4'}, 3: {'hotel_0_5'}, 4: {'hotel_0_7'}, 5: {'hotel_0_8'}, 6: {'hotel_0_12'}, 7: {'hotel_0_16'}, 8: {'hotel_0_17'}, 9: {'hotel_0_19'}, 10: {'hotel_0_20'}, 11: {'hotel_0_24'}, 12: {'hotel_0_25'}, 13: {'hotel_1_0'}, 14: {'hotel_1_2'}, 15: {'hotel_1_7'}, 16: {'hotel_1_9'}, 17: {'hotel_1_10'}, 18: {'hotel_1_12'}, 19: {'hotel_1_17'}, 20: {'hotel_1_20'}, 21: {'hotel_1_22'}, 22: {'hotel_1_25'}, 23: {'hotel_2_0'}, 24: {'hotel_2_2'}, 25: {'hotel_2_3'}, 26: {'hotel_2_4'}, 27: {'hotel_2_7'}, 28: {'hotel_2_14'}, 29: {'hotel_2_16'}, 30: {'hotel_2_17'}, 31: {'hotel_2_22'}, 32: {'hotel_2_25'}, 33: {'hotel_3_0'}, 34: {'hotel_3_2'}, 35: {'hotel_3_4'}, 36: {'hotel_3_7'}, 37: {'hotel_3_8'}, 38: {'hotel_3_9'}, 39: {'hotel_3_10'}, 40: {'hotel_3_11'}, 41: {'hotel_3_12'}, 42: {'hotel_3_13'}, 43: {'hotel_3_14'}, 44: {'hotel_3_16'}, 45: {'hotel_3_18'}, 46: {'hotel_3_27'}, 47: {'hotel_3_29'}, 48: {'hotel_3_33'}, 49: {'hotel_3_36'}, 50: {'hotel_4_6'}, 51: {'

## Merging

In [ ]:
merged_one_elem_cluster1 = _merge_eval(one_elem_cluster1, one_elem_cluster1, threshold = 0.9)
_store_cluster(merged_one_elem_cluster1, 'merged_one_elem_cluster1.pkl')

In [ ]:
len(one_elem_cluster1)

2414

In [ ]:
merged_one_elem_cluster2 = _merge_eval(one_elem_cluster2, one_elem_cluster2, threshold = 0.9)
_store_cluster(merged_one_elem_cluster2, 'merged_one_elem_cluster2.pkl')

In [ ]:
final_cluster4 = _merge_eval(final_cluster2, merged_one_elem_cluster, threshold = 0.85)
_store_cluster(final_cluster3, '__final4_merged_kb_doc_clusters.pkl')

#VII. Those missed

## Gather best cluster result from len > 1

In [ ]:
#Reorder final_cluster2 or ....
reordered_final_cluster2 = _reorder_cluster(final_cluster2)
_store_cluster(reordered_final_cluster2, 'reordered_final_cluster2.pkl')

{0: {'restaurant_120308_13', 'restaurant_120320_17', 'restaurant_120327_16', 'restaurant_120213_12', 'restaurant_120277_17', 'restaurant_120361_2', 'restaurant_120086_13', 'restaurant_120316_7', 'restaurant_120297_21', 'restaurant_120010_2', 'restaurant_120092_14', 'attraction_100030_0', 'restaurant_120304_17', 'restaurant_120178_1', 'restaurant_120470_19', 'hotel_16_13', 'restaurant_120390_12', 'restaurant_120226_17', 'restaurant_120188_9', 'restaurant_120439_15', 'restaurant_120351_12', 'restaurant_120230_13', 'attraction_100107_5', 'hotel_110049_0', 'restaurant_120388_15', 'restaurant_120074_15', 'restaurant_120159_14', 'restaurant_120201_14', 'attraction_100103_3', 'restaurant_120167_18', 'restaurant_120286_13', 'restaurant_120491_13', 'restaurant_120065_13', 'attraction_100189_2', 'restaurant_120195_14', 'restaurant_120397_14', 'attraction_100019_0', 'restaurant_120444_14', 'restaurant_120101_16', 'restaurant_120322_17', 'hotel_4_11', 'restaurant_120128_15', 'restaurant_120122_1',

In [ ]:
#Or get it if it is initialized
import pickle
w = open('reordered_final_cluster2.pkl','rb')
reordered_final_cluster2 = pickle.load(w)
print(reordered_final_cluster2, len(reordered_final_cluster2), sep = '\n')

{0: {'restaurant_120308_13', 'restaurant_120320_17', 'restaurant_120327_16', 'restaurant_120213_12', 'restaurant_120277_17', 'restaurant_120361_2', 'restaurant_120086_13', 'restaurant_120316_7', 'restaurant_120297_21', 'restaurant_120010_2', 'restaurant_120092_14', 'attraction_100030_0', 'restaurant_120304_17', 'restaurant_120178_1', 'restaurant_120470_19', 'hotel_16_13', 'restaurant_120390_12', 'restaurant_120226_17', 'restaurant_120188_9', 'restaurant_120439_15', 'restaurant_120351_12', 'restaurant_120230_13', 'attraction_100107_5', 'hotel_110049_0', 'restaurant_120388_15', 'restaurant_120074_15', 'restaurant_120159_14', 'restaurant_120201_14', 'attraction_100103_3', 'restaurant_120167_18', 'restaurant_120286_13', 'restaurant_120491_13', 'restaurant_120065_13', 'attraction_100189_2', 'restaurant_120195_14', 'restaurant_120397_14', 'attraction_100019_0', 'restaurant_120444_14', 'restaurant_120101_16', 'restaurant_120322_17', 'hotel_4_11', 'restaurant_120122_1', 'attraction_100033_3', 

## Gather the doc_ids missed and initialize one_elem_cluster

In [ ]:
id_lst = []

for cat in dic:
    for elem in dic[cat]:
        doc_lst = dic[cat][elem]['docs']
        for id in doc_lst:
            id_lst.append(doc_lst[id]['doc_id'])

print(len(id_lst))

for key in reordered_final_cluster2:
    cluster = reordered_final_cluster2[key]
    for id in cluster:
        if id in id_lst:
            id_lst.remove(id)

print(len(id_lst))

12039
832


In [ ]:
one_elem_cluster = {}
id = 0
for elem in id_lst:
    one_elem_cluster[id] = set({elem})
    id += 1
print(one_elem_cluster, len(one_elem_cluster), sep = '\n')
_store_cluster(one_elem_cluster, 'one_elem_cluster.pkl')


{0: {'hotel_0_2'}, 1: {'hotel_0_7'}, 2: {'hotel_0_20'}, 3: {'hotel_0_24'}, 4: {'hotel_0_25'}, 5: {'hotel_2_0'}, 6: {'hotel_2_7'}, 7: {'hotel_2_14'}, 8: {'hotel_2_22'}, 9: {'hotel_3_7'}, 10: {'hotel_3_18'}, 11: {'hotel_4_12'}, 12: {'hotel_4_21'}, 13: {'hotel_4_24'}, 14: {'hotel_4_27'}, 15: {'hotel_4_35'}, 16: {'hotel_5_5'}, 17: {'hotel_6_3'}, 18: {'hotel_6_14'}, 19: {'hotel_6_18'}, 20: {'hotel_7_8'}, 21: {'hotel_8_3'}, 22: {'hotel_8_10'}, 23: {'hotel_8_14'}, 24: {'hotel_8_16'}, 25: {'hotel_8_18'}, 26: {'hotel_8_25'}, 27: {'hotel_9_0'}, 28: {'hotel_9_19'}, 29: {'hotel_9_20'}, 30: {'hotel_10_21'}, 31: {'hotel_11_1'}, 32: {'hotel_11_28'}, 33: {'hotel_12_20'}, 34: {'hotel_12_21'}, 35: {'hotel_13_29'}, 36: {'hotel_13_33'}, 37: {'hotel_15_27'}, 38: {'hotel_16_29'}, 39: {'hotel_17_3'}, 40: {'hotel_17_5'}, 41: {'hotel_17_7'}, 42: {'hotel_17_20'}, 43: {'hotel_18_8'}, 44: {'hotel_18_11'}, 45: {'hotel_20_8'}, 46: {'hotel_20_15'}, 47: {'hotel_20_37'}, 48: {'hotel_21_8'}, 49: {'hotel_21_13'}, 50: {'

## Start Merging

The results of final_cluster2 (116) is used because it has been observed, and ambiguous list is based on final_cluster2. Although final_cluster3 has smaller amount of clusters (96), it merged some of the ambigious clusters from final_cluster2, making it a bit noisy

Notes:
1. From pattern it seems like here threshold = 0.7~ might be better.
2. Model doesn't do well when given pair is long sentence (that it has never seen before)

In [ ]:
final_cluster4 = _merge_eval(reordered_final_cluster2, one_elem_cluster, diff = True, threshold = 0.7, skip_ambig = True, manual = 0.33)
_store_cluster(final_cluster4, '__final4_merged_kb_doc_clusters.pkl')

Length of Final Cluster:	 183
{0: {'restaurant_120308_13', 'restaurant_120320_17', 'restaurant_120327_16', 'restaurant_120213_12', 'restaurant_120277_17', 'restaurant_120361_2', 'restaurant_120086_13', 'restaurant_120316_7', 'restaurant_120297_21', 'restaurant_120010_2', 'restaurant_120092_14', 'attraction_100030_0', 'restaurant_120304_17', 'restaurant_120178_1', 'restaurant_120470_19', 'hotel_16_13', 'restaurant_120390_12', 'restaurant_120226_17', 'restaurant_120188_9', 'restaurant_120439_15', 'restaurant_120351_12', 'restaurant_120230_13', 'attraction_100107_5', 'hotel_110049_0', 'restaurant_120388_15', 'restaurant_120074_15', 'restaurant_120159_14', 'hotel_110065_1', 'restaurant_120201_14', 'attraction_100103_3', 'restaurant_120167_18', 'restaurant_120286_13', 'restaurant_120491_13', 'restaurant_120065_13', 'attraction_100189_2', 'restaurant_120195_14', 'restaurant_120397_14', 'attraction_100019_0', 'restaurant_120444_14', 'restaurant_120101_16', 'restaurant_120322_17', 'hotel_4_11'

In [ ]:
print(final_cluster4[70])

{'restaurant_120482_15', 'restaurant_120456_16', 'restaurant_120212_14', 'restaurant_120407_14', 'restaurant_120030_19', 'restaurant_120256_20', 'restaurant_120293_16', 'restaurant_120053_19', 'restaurant_120212_13', 'restaurant_120033_19', 'restaurant_120019_16', 'restaurant_120424_18', 'restaurant_120003_17'}


In [ ]:
final_cluster5 = _merge_eval(final_cluster4, final_cluster4, threshold = 0.6, skip_ambig = True)
_store_cluster(final_cluster5, '__final5_merged_kb_doc_clusters.pkl')

2 examples -------------------
Size:	 2
Contents:
 [('Is there a fee to cross it?', 'No, it is not advised to ride the Flyer if you are pregnant.'), ("Could I ride The Flyer while I'm pregnant?", 'Yes, tolls are collected in the southbound direction into San Francisco only.')]
NO MERGE		------
SCORE ONLY	 0.0 < 0.6 


2 examples -------------------
Size:	 2
Contents:
 [('Is there a fee to cross it?', 'The maximum weight to ride the Flyer in San Francisco is 300 pounds.'), ('What is the maximum weight to ride the Flyer?', 'Yes, tolls are collected in the southbound direction into San Francisco only.')]
NO MERGE		------
SCORE ONLY	 0.0 < 0.6 


2 examples -------------------
Size:	 2
Contents:
 [("Could I ride The Flyer while I'm pregnant?", 'The maximum weight to ride the Flyer in San Francisco is 300 pounds.'), ('What is the maximum weight to ride the Flyer?', 'No, it is not advised to ride the Flyer if you are pregnant.')]
NO MERGE		------
SCORE ONLY	 0.0 < 0.6 


Length of Final Clus

##Evaluating Merge result

In [ ]:
#Initialize if stored
import pickle
f = open('__final5_merged_kb_doc_clusters.pkl', 'rb')
final_cluster5 = pickle.load(f)

In [ ]:
#Covers Everything? Should be 12039
finddupes(final_cluster5)

12039 {'hotel_110085_8': 1, 'hotel_17_7': 1, 'hotel_110138_5': 1, 'hotel_110049_8': 1, 'hotel_110080_11': 1, 'hotel_110026_22': 1, 'hotel_29_14': 1, 'hotel_110168_22': 1, 'hotel_110115_18': 1, 'hotel_110015_1': 1, 'hotel_110088_16': 1, 'hotel_110045_17': 1, 'hotel_110034_15': 1, 'hotel_23_9': 1, 'restaurant_120496_6': 1, 'hotel_23_6': 1, 'hotel_10_27': 1, 'hotel_6_13': 1, 'hotel_110076_23': 1, 'hotel_110028_20': 1, 'hotel_110183_5': 1, 'hotel_110012_8': 1, 'hotel_110029_12': 1, 'hotel_110013_20': 1, 'hotel_110046_13': 1, 'hotel_110006_19': 1, 'hotel_110182_23': 1, 'hotel_110095_23': 1, 'hotel_110037_20': 1, 'hotel_110110_12': 1, 'hotel_110178_15': 1, 'hotel_110016_17': 1, 'hotel_110167_20': 1, 'hotel_110135_19': 1, 'hotel_110151_20': 1, 'hotel_110104_25': 1, 'hotel_110142_21': 1, 'hotel_110120_21': 1, 'hotel_15_8': 1, 'hotel_110163_24': 1, 'hotel_110099_24': 1, 'hotel_110080_19': 1, 'hotel_110010_23': 1, 'hotel_110168_21': 1, 'hotel_110018_23': 1, 'hotel_110064_23': 1, 'hotel_110031_17

In [ ]:
print(final_cluster5, len(final_cluster5), sep = '\n')

{0: {'restaurant_120482_14', 'restaurant_120212_0', 'restaurant_120463_15', 'restaurant_120328_15', 'attraction_100042_5', 'restaurant_120275_18', 'restaurant_120512_12', 'hotel_13_4', 'restaurant_120527_11', 'attraction_100176_3', 'restaurant_120087_15', 'restaurant_120226_17', 'attraction_100040_2', 'restaurant_120102_17', 'attraction_100023_5', 'restaurant_120455_11', 'restaurant_120246_10', 'restaurant_120016_2', 'restaurant_120033_16', 'restaurant_120121_11', 'hotel_27_14', 'restaurant_120501_12', 'restaurant_120319_13', 'restaurant_120298_16', 'restaurant_120269_14', 'restaurant_120279_10', 'restaurant_120127_4', 'restaurant_120225_13', 'hotel_2_12', 'restaurant_120163_12', 'attraction_100054_8', 'restaurant_120385_12', 'attraction_100077_1', 'restaurant_120426_12', 'restaurant_120190_10', 'restaurant_120218_13', 'attraction_100131_4', 'restaurant_120050_16', 'restaurant_120438_13', 'restaurant_120108_16', 'restaurant_120510_11', 'restaurant_120150_20', 'restaurant_120448_15', 'a

In [ ]:
reordered_final_cluster5 = _reorder_cluster(final_cluster5)
_store_cluster(reordered_final_cluster5, 'reordered_final_cluster5.pkl')

{0: {'restaurant_120482_14', 'restaurant_120212_0', 'restaurant_120463_15', 'restaurant_120328_15', 'attraction_100042_5', 'restaurant_120275_18', 'restaurant_120512_12', 'hotel_13_4', 'restaurant_120527_11', 'attraction_100176_3', 'restaurant_120087_15', 'restaurant_120226_17', 'attraction_100040_2', 'restaurant_120102_17', 'attraction_100023_5', 'restaurant_120455_11', 'restaurant_120246_10', 'restaurant_120016_2', 'restaurant_120033_16', 'restaurant_120121_11', 'hotel_27_14', 'restaurant_120501_12', 'restaurant_120319_13', 'restaurant_120298_16', 'restaurant_120269_14', 'restaurant_120279_10', 'restaurant_120127_4', 'restaurant_120225_13', 'hotel_2_12', 'restaurant_120163_12', 'attraction_100054_8', 'restaurant_120385_12', 'attraction_100077_1', 'restaurant_120426_12', 'restaurant_120190_10', 'restaurant_120218_13', 'attraction_100131_4', 'restaurant_120050_16', 'restaurant_120438_13', 'restaurant_120108_16', 'restaurant_120510_11', 'restaurant_120150_20', 'restaurant_120448_15', 'a

In [ ]:
_get_result('reordered_final_cluster5_result.txt', reordered_final_cluster5)

Merge Again?

In [ ]:
final_cluster6 = _merge_eval(final_cluster5, final_cluster5, threshold = 0.55, skip_ambig = True, manual = 0.33)
_store_cluster(final_cluster5, '__final6_merged_kb_doc_clusters.pkl')

2 examples -------------------
Size:	 2
Contents:
 [('Is there a conserve available?', 'The maximum weight to ride the Flyer in San Francisco is 300 pounds.'), ('What is the maximum weight to ride the Flyer?', 'a conserve is available')]
NO MERGE		------
SCORE ONLY	 0.0 < 0.55 


Length of Final Cluster:	 130
{0: {'restaurant_120482_14', 'restaurant_120212_0', 'restaurant_120463_15', 'restaurant_120328_15', 'attraction_100042_5', 'restaurant_120275_18', 'restaurant_120512_12', 'hotel_13_4', 'restaurant_120527_11', 'attraction_100176_3', 'restaurant_120087_15', 'restaurant_120226_17', 'attraction_100040_2', 'restaurant_120102_17', 'attraction_100023_5', 'restaurant_120455_11', 'restaurant_120246_10', 'restaurant_120016_2', 'restaurant_120033_16', 'restaurant_120121_11', 'hotel_27_14', 'restaurant_120501_12', 'restaurant_120319_13', 'restaurant_120298_16', 'restaurant_120269_14', 'restaurant_120279_10', 'restaurant_120127_4', 'restaurant_120225_13', 'hotel_2_12', 'restaurant_120163_12', 

In [ ]:
final_cluster7 = _merge_eval(final_cluster6, final_cluster6, threshold = 0.5, skip_ambig = True, manual = 0.1)
_store_cluster(final_cluster5, '__final7_merged_kb_doc_clusters.pkl')

In [ ]:
print(final_cluster7, len(final_cluster7), sep = '\n')

{0: {'restaurant_120482_14', 'restaurant_120212_0', 'restaurant_120463_15', 'restaurant_120328_15', 'attraction_100042_5', 'restaurant_120275_18', 'restaurant_120512_12', 'hotel_13_4', 'restaurant_120527_11', 'attraction_100176_3', 'restaurant_120087_15', 'restaurant_120226_17', 'attraction_100040_2', 'restaurant_120102_17', 'attraction_100023_5', 'restaurant_120455_11', 'restaurant_120246_10', 'restaurant_120016_2', 'restaurant_120033_16', 'restaurant_120121_11', 'hotel_27_14', 'restaurant_120501_12', 'restaurant_120319_13', 'restaurant_120298_16', 'restaurant_120269_14', 'restaurant_120279_10', 'restaurant_120127_4', 'restaurant_120225_13', 'hotel_2_12', 'restaurant_120163_12', 'attraction_100054_8', 'restaurant_120385_12', 'attraction_100077_1', 'restaurant_120426_12', 'restaurant_120190_10', 'restaurant_120218_13', 'attraction_100131_4', 'restaurant_120050_16', 'restaurant_120438_13', 'restaurant_120108_16', 'restaurant_120510_11', 'restaurant_120150_20', 'restaurant_120448_15', 'a

#VIII. Output Labels

In [ ]:
#Make sure the final cluster we using is good to go
reordered_final_cluster7 = _reorder_cluster(final_cluster7)
print(reordered_final_cluster7, len(reordered_final_cluster7), sep = '\n')
_store_cluster(reordered_final_cluster7, 'reordered_final_cluster7.pkl')

{1: {'restaurant_120482_14', 'restaurant_120212_0', 'restaurant_120463_15', 'restaurant_120328_15', 'attraction_100042_5', 'restaurant_120275_18', 'restaurant_120512_12', 'hotel_13_4', 'restaurant_120527_11', 'attraction_100176_3', 'restaurant_120087_15', 'restaurant_120226_17', 'attraction_100040_2', 'restaurant_120102_17', 'attraction_100023_5', 'restaurant_120455_11', 'restaurant_120246_10', 'restaurant_120016_2', 'restaurant_120033_16', 'restaurant_120121_11', 'hotel_27_14', 'restaurant_120501_12', 'restaurant_120319_13', 'restaurant_120298_16', 'restaurant_120269_14', 'restaurant_120279_10', 'restaurant_120127_4', 'restaurant_120225_13', 'hotel_2_12', 'restaurant_120163_12', 'attraction_100054_8', 'restaurant_120385_12', 'attraction_100077_1', 'restaurant_120426_12', 'restaurant_120190_10', 'restaurant_120218_13', 'attraction_100131_4', 'restaurant_120050_16', 'restaurant_120438_13', 'restaurant_120108_16', 'restaurant_120510_11', 'restaurant_120150_20', 'restaurant_120448_15', 'a

In [ ]:
import pickle
w = open('reordered_final_cluster7.pkl','rb')
reordered_final_cluster7 = pickle.load(w)
print(reordered_final_cluster7, len(reordered_final_cluster7), sep = '\n')
_get_result('0821_final_res.txt', reordered_final_cluster7)

{1: {'restaurant_120045_13', 'attraction_100043_1', 'restaurant_120050_16', 'hotel_14_20', 'restaurant_120298_16', 'attraction_100114_2', 'restaurant_120185_21', 'restaurant_120315_12', 'restaurant_120100_15', 'restaurant_120519_11', 'restaurant_120230_13', 'restaurant_120052_9', 'restaurant_120262_13', 'attraction_100187_4', 'restaurant_120127_4', 'attraction_100165_3', 'restaurant_120150_20', 'restaurant_120423_14', 'restaurant_120085_12', 'restaurant_120031_10', 'hotel_31_20', 'restaurant_120450_14', 'restaurant_120329_13', 'restaurant_120465_18', 'restaurant_120318_14', 'restaurant_120033_16', 'hotel_7_12', 'attraction_100019_0', 'attraction_100023_5', 'restaurant_120293_16', 'restaurant_120013_15', 'restaurant_120398_1', 'restaurant_120010_2', 'hotel_6_18', 'attraction_100183_2', 'restaurant_120195_14', 'hotel_8_8', 'attraction_100029_3', 'attraction_100077_1', 'attraction_100115_2', 'restaurant_120087_15', 'restaurant_120323_13', 'attraction_100092_6', 'restaurant_120134_7', 'res

In [ ]:
import json

out = open('kb_eval_final.json','w')
for key in reordered_final_cluster7:
    for id in reordered_final_cluster7[key]:
        cat,elem,doc_id = id.split('_')
        doc_lst = dic[cat][elem]['docs']
        if 'intent_label' not in doc_lst[doc_id]:
            doc_lst[doc_id]['intent_label'] = key

json.dump(dic, out, indent=4)
out.close()

#IX. Manual Improvements

In [ ]:
%env HOME=/content/drive/MyDrive/
#Enter Model Environment
%cd ~/Research/ner/text_classifier/final_results
!ls -lrt

env: HOME=/content/drive/MyDrive/
/content/drive/MyDrive/Research/ner/text_classifier/final_results
total 13137
-rw------- 1 root root     1354 Aug 31 15:56 reference.csv
-rw------- 1 root root 13121389 Aug 31 16:45 kb_eval_final.json
-rw------- 1 root root        0 Aug 31 22:16 finale_res.txt
-rw------- 1 root root   328693 Aug 31 22:16 finale.pkl


In [ ]:
import pickle
w = open('/content/drive/MyDrive/Research/ner/text_classifier/reordered_final_cluster7.pkl','rb')
reordered_final_cluster7 = pickle.load(w)
print(reordered_final_cluster7, len(reordered_final_cluster7), sep = '\n')

{1: {'restaurant_120240_7', 'restaurant_120027_14', 'restaurant_120384_11', 'restaurant_120095_9', 'restaurant_120122_1', 'restaurant_120318_14', 'restaurant_120150_20', 'attraction_100023_5', 'attraction_100072_1', 'attraction_100045_2', 'restaurant_120064_14', 'attraction_100042_5', 'restaurant_120052_9', 'restaurant_120008_18', 'restaurant_120053_19', 'restaurant_120455_11', 'restaurant_120453_0', 'restaurant_120201_14', 'restaurant_120107_12', 'attraction_100040_2', 'restaurant_120020_9', 'restaurant_120015_17', 'restaurant_120450_14', 'restaurant_120388_15', 'attraction_100057_3', 'restaurant_120033_16', 'hotel_14_20', 'restaurant_120087_15', 'restaurant_120206_13', 'restaurant_120094_13', 'attraction_100197_2', 'attraction_100030_0', 'restaurant_120130_14', 'restaurant_120349_17', 'restaurant_120282_17', 'attraction_100022_2', 'restaurant_120344_14', 'restaurant_120239_17', 'restaurant_120440_18', 'restaurant_120065_13', 'restaurant_120192_16', 'restaurant_120023_11', 'restaurant

In [ ]:
ref_dic = {}

f1 = open('reference.csv', 'r')
f1.readline()
for line in f1:
    values = line.split(',')
    doc_id = values[0].strip()
    curr_cid = values[1].strip()
    correct_cid = values[2].strip()
    if doc_id not in ref_dic:
        ref_dic[doc_id] = (curr_cid,correct_cid)
    else:
        print(doc_id)#should only be one (restaurant_120064_19)
    
f1.close()
print(ref_dic)

restaurant_120064_19
{'hotel_110034_15': ('7', '11'), 'hotel_110045_17': ('7', '11'), 'attraction_100172_0': ('16', '76'), 'restaurant_120100_10': ('18', '53'), 'hotel_110099_11': ('30', '31'), 'restaurant_120065_0': ('30', '33'), 'restaurant_120071_2': ('42', '62'), 'hotel_110191_9': ('42', '18'), 'hotel_110043_13': ('42', '18'), 'restaurant_120213_9': ('42', '69'), 'restaurant_120065_8': ('42', '2'), 'restaurant_120021_5': ('42', '2'), 'restaurant_120031_6': ('42', '3'), 'hotel_110168_25': ('42', '7'), 'restaurant_120087_10': ('42', '49'), 'hotel_110163_15': ('42', '22'), 'hotel_110037_23': ('42', '7'), 'hotel_110047_9': ('42', '7'), 'restaurant_120407_8': ('42', '50'), 'restaurant_120065_1': ('42', '22'), 'restaurant_120196_8': ('42', '23'), 'restaurant_19220_0': ('6', '45'), 'restaurant_120283_4': ('6', '45'), 'restaurant_19177_4': ('6', '45'), 'restaurant_19230_4': ('6', '45'), 'restaurant_120154_10': ('6', '45'), 'restaurant_19213_5': ('47', '19'), 'restaurant_7492_2': ('47', '19

In [ ]:
for doc_id in ref_dic:
    key_to_delete = int(ref_dic[doc_id][0])
    key_to_add = int(ref_dic[doc_id][1])
    reordered_final_cluster7[key_to_delete].remove(doc_id)
    reordered_final_cluster7[key_to_add].add(doc_id)
    #print(reordered_final_cluster7[key_to_add])


In [ ]:
print(reordered_final_cluster7, len(reordered_final_cluster7), sep = '\n')

{1: {'restaurant_120240_7', 'restaurant_120027_14', 'restaurant_120384_11', 'restaurant_120095_9', 'restaurant_120122_1', 'restaurant_120318_14', 'restaurant_120150_20', 'attraction_100023_5', 'attraction_100072_1', 'attraction_100045_2', 'restaurant_120064_14', 'attraction_100042_5', 'restaurant_120052_9', 'restaurant_120008_18', 'restaurant_120053_19', 'restaurant_120455_11', 'restaurant_120453_0', 'restaurant_120201_14', 'restaurant_120107_12', 'attraction_100040_2', 'restaurant_120020_9', 'restaurant_120015_17', 'restaurant_120450_14', 'restaurant_120388_15', 'attraction_100057_3', 'restaurant_120033_16', 'hotel_14_20', 'restaurant_120087_15', 'restaurant_120206_13', 'restaurant_120094_13', 'attraction_100197_2', 'attraction_100030_0', 'restaurant_120130_14', 'restaurant_120349_17', 'restaurant_120282_17', 'attraction_100022_2', 'restaurant_120344_14', 'restaurant_120239_17', 'restaurant_120440_18', 'restaurant_120065_13', 'restaurant_120192_16', 'restaurant_120023_11', 'restaurant

In [ ]:
merge_map = {
    3:[4,95],
    11:[13],
    8:[17],
    25:[29],
    19:[41],
    2:[64,66,67],
    47:[68],
    44:[50,74],
    10:[79],
    7:[87],
    33:[88],
    6:[92],
    34:[94],
    58:[97],
    47:[101],
    98:[99,100],
    106:[107,108],
    18:[109,110],
    63:[111],
    76:[112],
    89:[118],
    113:[114,115],
    122:[120,119],
    102:[124],
    113:[125],
}

In [ ]:
#Check for possible errors merging and deleting something that will be merged in the future
key_lst = []
for entry in merge_map:
    if entry not in key_lst:
        key_lst.append(entry)
    if merge_map[entry] in key_lst:
        print('Error with', entry, merge_map[entry])
key_lst = []
for entry in merge_map:
    if entry not in key_lst:
        key_lst.append(entry)
    else:
        print('Error with', entry)

In [ ]:
for key_cluster in merge_map:
    keys_to_merge = merge_map[key_cluster]
    for key_to_merge in keys_to_merge:
        reordered_final_cluster7[key_cluster] |= reordered_final_cluster7[key_to_merge]
        reordered_final_cluster7.pop(key_to_merge)
print(reordered_final_cluster7, len(reordered_final_cluster7), sep = '\n')

{1: {'restaurant_120240_7', 'restaurant_120027_14', 'restaurant_120384_11', 'restaurant_120095_9', 'restaurant_120122_1', 'restaurant_120318_14', 'restaurant_120150_20', 'attraction_100023_5', 'attraction_100072_1', 'attraction_100045_2', 'restaurant_120064_14', 'attraction_100042_5', 'restaurant_120052_9', 'restaurant_120008_18', 'restaurant_120053_19', 'restaurant_120455_11', 'restaurant_120453_0', 'restaurant_120201_14', 'restaurant_120107_12', 'attraction_100040_2', 'restaurant_120020_9', 'restaurant_120015_17', 'restaurant_120450_14', 'restaurant_120388_15', 'attraction_100057_3', 'restaurant_120033_16', 'hotel_14_20', 'restaurant_120087_15', 'restaurant_120206_13', 'restaurant_120094_13', 'attraction_100197_2', 'attraction_100030_0', 'restaurant_120130_14', 'restaurant_120349_17', 'restaurant_120282_17', 'attraction_100022_2', 'restaurant_120344_14', 'restaurant_120239_17', 'restaurant_120440_18', 'restaurant_120065_13', 'restaurant_120192_16', 'restaurant_120023_11', 'restaurant

In [ ]:
reordered_final_cluster7[3]

In [ ]:
dupes = finddupes(reordered_final_cluster7)

12039 {'hotel_110015_1': 1, 'hotel_110088_16': 1, 'hotel_110183_5': 1, 'hotel_23_6': 1, 'restaurant_120496_6': 1, 'hotel_10_27': 1, 'hotel_6_13': 1, 'hotel_110192_1': 1, 'hotel_110125_1': 1, 'restaurant_19237_6': 1, 'restaurant_19210_12': 1, 'restaurant_19218_4': 1, 'restaurant_19176_14': 1, 'restaurant_120010_4': 1, 'hotel_110131_16': 1, 'restaurant_120401_14': 1, 'restaurant_19177_9': 1, 'restaurant_19183_10': 1, 'hotel_21_16': 1, 'hotel_110099_19': 1, 'hotel_110084_18': 1, 'hotel_10_2': 1, 'hotel_110200_3': 1, 'hotel_26_6': 1, 'hotel_110182_11': 1, 'hotel_110182_4': 1, 'hotel_110037_11': 1, 'hotel_110088_11': 1, 'hotel_110194_10': 1, 'hotel_110034_10': 1, 'hotel_110154_15': 1, 'hotel_110117_6': 1, 'restaurant_120188_8': 1, 'restaurant_120163_4': 1, 'restaurant_120480_16': 1, 'restaurant_120218_3': 1, 'restaurant_120195_2': 1, 'restaurant_120174_16': 1, 'restaurant_120439_18': 1, 'restaurant_120327_17': 1, 'restaurant_120333_17': 1, 'restaurant_120107_1': 1, 'attraction_100143_1': 1,

In [ ]:
for entry in dupes:
    if dupes[entry] > 1:
        print('Dupe in ',entry)
#No dupes! great!

In [ ]:
#Remove empties
#keys_to_del = []
#for key in reordered_final_cluster7:
#    if len(reordered_final_cluster7[key]) == 0:
#        key_to_del.append(key)

for (key,val) in reordered_final_cluster7.items():
    if len(val) == 0:
        raise Exception('bitch')
        #del reordered_final_cluster7[key]

In [ ]:
print(reordered_final_cluster7, len(reordered_final_cluster7), sep = '\n')

{1: {'restaurant_120240_7', 'restaurant_120027_14', 'restaurant_120384_11', 'restaurant_120095_9', 'restaurant_120122_1', 'restaurant_120318_14', 'restaurant_120150_20', 'attraction_100023_5', 'attraction_100072_1', 'attraction_100045_2', 'restaurant_120064_14', 'attraction_100042_5', 'restaurant_120052_9', 'restaurant_120008_18', 'restaurant_120053_19', 'restaurant_120455_11', 'restaurant_120453_0', 'restaurant_120201_14', 'restaurant_120107_12', 'attraction_100040_2', 'restaurant_120020_9', 'restaurant_120015_17', 'restaurant_120450_14', 'restaurant_120388_15', 'attraction_100057_3', 'restaurant_120033_16', 'hotel_14_20', 'restaurant_120087_15', 'restaurant_120206_13', 'restaurant_120094_13', 'attraction_100197_2', 'attraction_100030_0', 'restaurant_120130_14', 'restaurant_120349_17', 'restaurant_120282_17', 'attraction_100022_2', 'restaurant_120344_14', 'restaurant_120239_17', 'restaurant_120440_18', 'restaurant_120065_13', 'restaurant_120192_16', 'restaurant_120023_11', 'restaurant

In [ ]:
import pickle
final = _reorder_cluster(reordered_final_cluster7)
w = open('finale.pkl','wb')
pickle.dump(final,w)
w.close()
_get_result('finale_res.txt',final)

In [ ]:
#Now output new labels to kb
import json

out = open('kb_eval_final.json','w')
for key in final:
    for id in final[key]:
        cat,elem,doc_id = id.split('_')
        doc_lst = dic[cat][elem]['docs']
        if 'intent_label' not in doc_lst[doc_id]:
            doc_lst[doc_id]['intent_label'] = key

json.dump(dic, out, indent=4)
out.close()